In [1]:
from graph_tool import getMap

import pandas as pd
import numpy as np

from tqdm import tqdm

# How to run on windows
# https://towardsdatascience.com/pandaral-lel-a-simple-and-efficient-tool-to-parallelize-your-pandas-operations-on-all-your-cpus-bb5ff2a409ae
from pandarallel import pandarallel
pandarallel.initialize(progress_bar=True)

import reverse_geocoder as rg
from global_land_mask import globe

INFO: Pandarallel will run on 12 workers.
INFO: Pandarallel will use Memory file system to transfer data between the main process and workers.


In [2]:
events = pd.read_pickle("events_all.pickle")

In [3]:
len(events)

423405

In [4]:
events.to_csv("events_all.csv", index=False)

In [5]:
df = pd.read_csv("events_all.csv")
df["country"] = ""

In [6]:
df[:10]

event_id          event_start  event_area  event_length  event_si  \
0  199900001  1999-01-01 00:00:00        0.01             1       0.0   
1  199900002  1999-01-01 00:00:00        0.06             3       0.0   
2  199900002  1999-01-01 00:00:00        0.06             3       0.0   
3  199900002  1999-01-01 00:00:00        0.06             3       0.0   
4  199900003  1999-01-01 00:00:00        0.03             2       0.0   
5  199900003  1999-01-01 00:00:00        0.03             2       0.0   
6  199900004  1999-01-01 00:00:00        0.16             1       0.0   
7  199900005  1999-01-01 01:00:00        0.01             1       0.0   
8  199900006  1999-01-01 01:00:00        0.03             2       0.0   
9  199900006  1999-01-01 01:00:00        0.03             2       0.0   

                  date  area        lat     latMax    lon  lonMax  maxPrec  \
0  1999-01-01 00:00:00  0.01  44.439999  44.439999   8.64    8.64     7.48   
1  1999-01-01 00:00:00  0.04  43.310001  43.360001   6.57    6.71     9.85   
2  1999-01-01 01:00:00  0.06  43.349998  43.360001   6.63    6.71     9.46   
3  1999-01-01 02:00:00  0.01  43.480000  43.480000   6.83    6.83     7.20   
4  1999-01-01 00:00:00  0.01  39.369999  39.369999  10.18   10.18     5.42   
5  1999-01-01 01:00:00  0.03  39.320000  39.369999  10.18   10.18     6.07   
6  1999-01-01 00:00:00  0.16  37.040001  36.970001  13.74   13.99    11.79   
7  1999-01-01 01:00:00  0.01  41.090000  41.090000   7.32    7.32     6.77   
8  1999-01-01 01:00:00  0.03  39.709999  39.770000   9.63    9.70     8.36   
9  1999-01-01 02:00:00  0.01  39.770000  39.770000   9.70    9.70     8.06   

   meanPre   si  size  stdv country  
0     7.48  0.0     1  0.00          
1     8.37  0.0     3  1.14          
2     7.87  0.0     4  0.94          
3     7.20  0.0     1  0.00          
4     5.42  0.0     1  0.00          
5     5.96  0.0     2  0.11          
6     8.44  0.0    11  1.50          
7     6.77  0.0     1  0.00          
8     6.86  0.0     2  1.50          
9     8.06  0.0     1  0.00

In [7]:
def add_country_func(row):
    current_lat = row["lat"]
    current_long = row["lon"]
    
    isLand = globe.is_land(current_lat, current_long)
    if(isLand):
        current_country = rg.search((current_lat, current_long), mode=1)[0]["cc"]
        row['country'] = current_country
    else:
        row['country'] = None
    
    return row

In [8]:
new_df = df.parallel_apply(add_country_func, axis=1)

Loading formatted geocoded file...Loading formatted geocoded file...Loading formatted geocoded file...Loading formatted geocoded file...Loading formatted geocoded file...Loading formatted geocoded file...Loading formatted geocoded file...Loading formatted geocoded file...



Loading formatted geocoded file...

Loading formatted geocoded file...



Loading formatted geocoded file...Loading formatted geocoded file...



In [9]:
new_df[:10]

event_id          event_start  event_area  event_length  event_si  \
0  199900001  1999-01-01 00:00:00        0.01             1       0.0   
1  199900002  1999-01-01 00:00:00        0.06             3       0.0   
2  199900002  1999-01-01 00:00:00        0.06             3       0.0   
3  199900002  1999-01-01 00:00:00        0.06             3       0.0   
4  199900003  1999-01-01 00:00:00        0.03             2       0.0   
5  199900003  1999-01-01 00:00:00        0.03             2       0.0   
6  199900004  1999-01-01 00:00:00        0.16             1       0.0   
7  199900005  1999-01-01 01:00:00        0.01             1       0.0   
8  199900006  1999-01-01 01:00:00        0.03             2       0.0   
9  199900006  1999-01-01 01:00:00        0.03             2       0.0   

                  date  area        lat     latMax    lon  lonMax  maxPrec  \
0  1999-01-01 00:00:00  0.01  44.439999  44.439999   8.64    8.64     7.48   
1  1999-01-01 00:00:00  0.04  43.310001  43.360001   6.57    6.71     9.85   
2  1999-01-01 01:00:00  0.06  43.349998  43.360001   6.63    6.71     9.46   
3  1999-01-01 02:00:00  0.01  43.480000  43.480000   6.83    6.83     7.20   
4  1999-01-01 00:00:00  0.01  39.369999  39.369999  10.18   10.18     5.42   
5  1999-01-01 01:00:00  0.03  39.320000  39.369999  10.18   10.18     6.07   
6  1999-01-01 00:00:00  0.16  37.040001  36.970001  13.74   13.99    11.79   
7  1999-01-01 01:00:00  0.01  41.090000  41.090000   7.32    7.32     6.77   
8  1999-01-01 01:00:00  0.03  39.709999  39.770000   9.63    9.70     8.36   
9  1999-01-01 02:00:00  0.01  39.770000  39.770000   9.70    9.70     8.06   

   meanPre   si  size  stdv country  
0     7.48  0.0     1  0.00      IT  
1     8.37  0.0     3  1.14      FR  
2     7.87  0.0     4  0.94      FR  
3     7.20  0.0     1  0.00      FR  
4     5.42  0.0     1  0.00    None  
5     5.96  0.0     2  0.11    None  
6     8.44  0.0    11  1.50    None  
7     6.77  0.0     1  0.00    None  
8     6.86  0.0     2  1.50      IT  
9     8.06  0.0     1  0.00    None

In [10]:
new_df.to_pickle("events_all_with_countries.pickle")

### Test on Map

In [11]:
events = pd.read_pickle("events_all_with_countries.pickle")

In [15]:
getMap(events[events['country'] == "DE"])